In [1]:
import pandas as pd
import numpy as np
from sklearn.feature_extraction.text import TfidfVectorizer, CountVectorizer
from sklearn.metrics.pairwise import cosine_similarity
import nltk
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from nltk.stem import PorterStemmer
import re
from sklearn.metrics.pairwise import cosine_similarity
import matplotlib.pyplot as plt

In [2]:
# read data
import pandas as pd
df = pd.read_csv('C:/Users/acer/OneDrive/Documents/coolyeah/SEM 5/NLP/uas/Data NLP Fix.csv')
gt = pd.read_csv('C:/Users/acer/OneDrive/Documents/coolyeah/SEM 5/NLP/uas/List Query NLP - Index Ground Truth.csv', sep = ',') #ground truth 30 query



In [3]:
df.head()

Index                                               Link  \
0      0  https://www.eatingwell.com/eva-longoria-loaded...   
1      1  https://www.eatingwell.com/french-onion-cabbag...   
2      2  https://www.eatingwell.com/cheesy-cabbage-grat...   
3      3  https://www.eatingwell.com/pumpkin-summer-squa...   
4      4  https://www.eatingwell.com/orange-chicken-broc...   

                                            Headline   Author Name  \
0  Eva Longoria’s 5-Ingredient Loaded Sweet Potatoes  Eva Longoria   
1  French Onion Cabbage Soup Is a Fun Twist on th...  Melissa Gray   
2   Making Cheesy Cabbage Gratin Is Worth the Effort    Julia Levy   
3  Pumpkin-Summer Squash Ravioli with Brown Butte...    Julia Levy   
4  This Orange Chicken &amp; Broccoli Skillet Is ...    Liv Dansky   

                                             Details  \
0  {'Active Time:': '20 mins', 'Total Time:': '1 ...   
1  {'Active Time:': '55 mins', 'Total Time:': '1 ...   
2  {'Active Time:': '40 mins', 'Total Time:': '1 ...   
3  {'Active Time:': '35 mins', 'Total Time:': '45...   
4  {'Active Time:': '30 mins', 'Total Time:': '1 ...   

                                         Description  \
0  Eva Longoria’s Loaded Sweet Potatoes, from her...   
1  This French onion cabbage soup is a creative t...   
2  This cheesy cabbage gratin puts a fresh spin o...   
3  This squash ravioli is like traditional raviol...   
4  This protein-packed orange chicken and broccol...   

                                          Infomation  \
0  ['No Added Sugar', 'Sesame-Free', 'Nut-Free', ...   
1  ['No Added Sugar', 'Gut Healthy', 'Mediterrane...   
2  ['No Added Sugar', 'Sesame-Free', 'Nut-Free', ...   
3  ['No Added Sugar', 'Sesame-Free', 'Soy-Free', ...   
4  ['Mediterranean Diet', 'Nut-Free', 'Dairy-Free...   

                                           Nutrition  \
0  {'Total Carbohydrate': '34g', 'Dietary Fiber':...   
1  {'fat': '19g', 'saturated fat': '5g', 'cholest...   
2  {'Total Carbohydrate': '14g', 'Dietary Fiber':...   
3  {'Total Carbohydrate': '16g', 'Dietary Fiber':...   
4  {'fat': '29g', 'saturated fat': '7g', 'cholest...   

                                             Serving  Rating  Rating Count  \
0  {'Servings Per Recipe': '4', 'Serving Size': '...     5.0             1   
1  {'Serving Size': ' about 1½ cups soup & ¾ cup ...     5.0             2   
2  {'Servings Per Recipe': '8', 'Serving Size': '...     5.0             2   
3  {'Servings Per Recipe': '4', 'Serving Size': '...     5.0             2   
4  {'Serving Size': ' 1 chicken thigh & about ¾ c...     5.0             3   

               Category       Cuisine  \
0            ['Dinner']  ['American']   
1  ['Dinner', 'Entree']  ['American']   
2            ['Dinner']  ['American']   
3            ['Dinner']  ['American']   
4            ['Dinner']  ['American']   

                                         Ingredients  \
0  ['4 large sweet potatoes', '6 slices bacon', '...   
1  ['6 tablespoons vegetable oil, divided', '1 sm...   
2  ['1 (2¼–2½ pound) head Savoy or green cabbage,...   
3  ['1¼ pounds yellow summer squash, trimmed (abo...   
4  ['1 tablespoon canola oil', '6 (6-ounce) bone-...   

                                         Instruction  
0  ['Preheat the oven to 400℉. Line a baking shee...  
1  ['Heat 2 tablespoons oil in a large Dutch oven...  
2  ['Preheat oven to 350°F. Coat a 3-quart oval, ...  
3  ['Preheat oven to 425°F with racks in top thir...  
4  ['Preheat oven to 350°F. Heat 1 tablespoon oil...

### Dataset

In [3]:
df= df[["Index","Headline",	"Author Name",	"Details",	"Description",	"Infomation",	"Nutrition",	"Serving",	"Rating",	"Rating Count",	"Category",	"Cuisine",	"Ingredients",	"Instruction"]]

### Preprocessing

In [4]:
import pandas as pd
import re
import nltk
from nltk.stem import WordNetLemmatizer
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords

# Download required NLTK resources
nltk.download('punkt')
nltk.download('wordnet')
nltk.download('stopwords')

# Initialize the lemmatizer
lemmatizer = WordNetLemmatizer()
stop_words = set(stopwords.words('english'))

def preprocess_text(text):
    if pd.isna(text):
        return ""
    text = str(text).lower()
    text = re.sub(r"[{}:.,!?;\"'()\-]", "", text)  
    text = re.sub(r"Â", "", text)    
    text = re.sub(r"[^\x00-\x7F]+", "", text)  
    text = re.sub(r"\s+", " ", text).strip()   
    tokens = word_tokenize(text) 

    filtered_tokens = [lemmatizer.lemmatize(token) for token in tokens if token not in stop_words]

    return ' '.join(filtered_tokens)  

df = df.drop_duplicates()

df['dokumen'] = df['Headline'] + ' ' + df['Author Name'] + ' ' +  df['Description'] + ' ' + df['Infomation'] + ' ' +  df['Category'] + ' ' + df['Cuisine'] + ' ' +  df['Ingredients'] + ' ' + df['Instruction']

# Apply preprocessing to the 'dokumen' column
df['processed_text'] = df['dokumen'].apply(preprocess_text)

# Display the desired columns
result = df[['Index', 'Headline', 'processed_text']]
print(result)


[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\acer\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\acer\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\acer\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


      Index                                           Headline  \
0         0  Eva Longoria’s 5-Ingredient Loaded Sweet Potatoes   
1         1  French Onion Cabbage Soup Is a Fun Twist on th...   
2         2   Making Cheesy Cabbage Gratin Is Worth the Effort   
3         3  Pumpkin-Summer Squash Ravioli with Brown Butte...   
4         4  This Orange Chicken &amp; Broccoli Skillet Is ...   
...     ...                                                ...   
5180   6802         Slow-Cooker Korean Beef &amp; Cabbage Stew   
5181   6803                      One-Pot Creamy Vegetable Soup   
5182   6804                     Slow-Cooker Carrot-Leek Bisque   
5183   6805     Slow-Cooker Italian Vegetable &amp; Farro Soup   
5184   6865               How to Make Popcorn in the Microwave   

                                         processed_text  
0     eva longorias 5ingredient loaded sweet potato ...  
1     french onion cabbage soup fun twist classic me...  
2     making cheesy cabbage grati

## DF Pertanyaan

In [5]:
import pandas as pd

# Define the data
data = {
    "pertanyaan": [
        "Any dinner recipes?",
        "Which recipes include both chicken and broccoli as ingredients and have a Mediterranean diet classification?",
        "Are there nut-free recipes?",
        "Gluten-free recipes for diet.",
        "Vegan dinner recipes categorized as low-carb.",
        "High-protein recipes containing quinoa as a primary ingredient.",
        "Asian dinner food.",
        "Dessert from America.",
        "Dishes free from added sugar.",
        "Dessert with chocolate.",
        "High protein meal for vegetarian.",
        "Low sugar and less than 150 calories drink suitable for diabetic.",
        "No-bake dessert recipes that are simple and quick to make.",
        "Provide meal prep recipes designed for weight loss with no seafood.",
        "Low-carb and high protein meals suitable for keto diet.",
        "Plant-based recipes high in iron for vegans.",
        "Low-sodium soups with fresh ingredients.",
        "Up to 4.5 star ratings smoothie bowl with banana.",
        "Fermented drinks for gut health and digestion.",
        "Low calorie dinner meal with lamb.",
        "Show me a recipe with sweet potatoes.",
        "I need a Mediterranean Diet dinner recipe.",
        "What are the recipes authored by Julia Levy?",
        "Can you show me a vegetarian soup recipe?",
        "Show recipes with a rating greater than 4 stars and chicken as a main ingredient.",
        "Do you have any protein-packed chicken dishes?",
        "Find me recipes for dinner?",
        "List breakfast recipes with a 5-star rating.",
        "Can you show nut-free Mexican recipes?",
        "Find me a dish without added sugar.",
        "I want mexican food no pork",
        "Give me a vegan recipe under 20 minutes.",
        "Find me a dessert recipe under 100 calories.",
        "Breakfast recipe with egg free.",
        "Soup recipe for 4 servings.",
        "I want a snack recipe with high protein.",
        "Give me a salmon recipe with no oven required.",
        "Breakfast recipe for lactose intolerant.",
        "Recipe for bone health.",
        "Give me a dessert recipe that is diabetes friendly.",
        "Peanut butter pancakes for breakfast.",
        "Cook shrimp pad Thai.",
        "Egg-avocado breakfast sandwich.",
        "Broccoli and sun-dried tomato pasta salad recipe.",
        "Smoothie recipes with antioxidants.",
        "Easy lemon recipes.",
        "Pumpkin sugar cookies that stay soft.",
        "Quinoa salad with feta, olives, and tomatoes.",
        "Penne with tuna and sun-dried tomatoes.",
        "Recipe for a cucumber sandwich.",
        "Show me a recipe with lamb and garlic.",
        "I need a breakfast recipe that serves two people less than 30 minutes.",
        "Show me a recipe provided by Liv Dansky.",
        "I am looking for a slow cooker recipe that takes more than 3 hours.",
        "Find me some dish that didn't add any kind of beans.",
        "List a recipe for a 5-star rating chicken dish.",
        "Show recipes for Asia continent.",
        "Looking for a cake with low calories.",
        "Show me a recipe without any milk or lactose.",
        "Give me a diet dish that contains no vegetables."
    ]
}

df_pertanyaan = pd.DataFrame(data)

df_pertanyaan['processed_pertanyaan'] = df_pertanyaan['pertanyaan'].apply(lambda text: pd.Series(preprocess_text(text)))

# Hasil akhir
df_pertanyaan

pertanyaan  \
0                                 Any dinner recipes?   
1   Which recipes include both chicken and broccol...   
2                         Are there nut-free recipes?   
3                       Gluten-free recipes for diet.   
4       Vegan dinner recipes categorized as low-carb.   
5   High-protein recipes containing quinoa as a pr...   
6                                  Asian dinner food.   
7                               Dessert from America.   
8                       Dishes free from added sugar.   
9                             Dessert with chocolate.   
10                  High protein meal for vegetarian.   
11  Low sugar and less than 150 calories drink sui...   
12  No-bake dessert recipes that are simple and qu...   
13  Provide meal prep recipes designed for weight ...   
14  Low-carb and high protein meals suitable for k...   
15       Plant-based recipes high in iron for vegans.   
16           Low-sodium soups with fresh ingredients.   
17  Up to 4.5 star ratings smoothie bowl with banana.   
18     Fermented drinks for gut health and digestion.   
19                 Low calorie dinner meal with lamb.   
20              Show me a recipe with sweet potatoes.   
21         I need a Mediterranean Diet dinner recipe.   
22       What are the recipes authored by Julia Levy?   
23          Can you show me a vegetarian soup recipe?   
24  Show recipes with a rating greater than 4 star...   
25     Do you have any protein-packed chicken dishes?   
26                        Find me recipes for dinner?   
27       List breakfast recipes with a 5-star rating.   
28             Can you show nut-free Mexican recipes?   
29                Find me a dish without added sugar.   
30                        I want mexican food no pork   
31           Give me a vegan recipe under 20 minutes.   
32       Find me a dessert recipe under 100 calories.   
33                    Breakfast recipe with egg free.   
34                        Soup recipe for 4 servings.   
35           I want a snack recipe with high protein.   
36     Give me a salmon recipe with no oven required.   
37           Breakfast recipe for lactose intolerant.   
38                            Recipe for bone health.   
39  Give me a dessert recipe that is diabetes frie...   
40              Peanut butter pancakes for breakfast.   
41                              Cook shrimp pad Thai.   
42                    Egg-avocado breakfast sandwich.   
43  Broccoli and sun-dried tomato pasta salad recipe.   
44                Smoothie recipes with antioxidants.   
45                                Easy lemon recipes.   
46              Pumpkin sugar cookies that stay soft.   
47      Quinoa salad with feta, olives, and tomatoes.   
48            Penne with tuna and sun-dried tomatoes.   
49                    Recipe for a cucumber sandwich.   
50             Show me a recipe with lamb and garlic.   
51  I need a breakfast recipe that serves two peop...   
52           Show me a recipe provided by Liv Dansky.   
53  I am looking for a slow cooker recipe that tak...   
54  Find me some dish that didn't add any kind of ...   
55    List a recipe for a 5-star rating chicken dish.   
56                   Show recipes for Asia continent.   
57              Looking for a cake with low calories.   
58      Show me a recipe without any milk or lactose.   
59   Give me a diet dish that contains no vegetables.   

                                 processed_pertanyaan  
0                                       dinner recipe  
1   recipe include chicken broccoli ingredient med...  
2                                      nutfree recipe  
3                              glutenfree recipe diet  
4             vegan dinner recipe categorized lowcarb  
5   highprotein recipe containing quinoa primary i...  
6                                   asian dinner food  
7                                     dessert america  
8                               dish free added sugar  
9    

In [7]:
# Count the number of questions
question_count = len(data["pertanyaan"])
print(question_count)

60


In [6]:
import pandas as pd

# Baca data ground truth
ground_truth = gt

# Inisialisasi dictionary ground_truth_dict
ground_truth_dict = {}

# Iterasi melalui kolom yang dimulai dengan 'q' untuk setiap pertanyaan
for col in ground_truth.columns:
    if col.startswith('q'):  # Hanya proses kolom yang diawali 'q'
        # Buat nama kunci dictionary berdasarkan kolom
        question_key = f"Pertanyaan {col[1:]}"  # 'q1' -> 'Pertanyaan 1'
        
        # Ambil nilai unik dari kolom (tanpa NaN)
        ground_truth_dict[question_key] = set(ground_truth[col].dropna().astype(int).tolist())

# Tampilkan hasil ground_truth_dict
print(ground_truth_dict)



{'Pertanyaan 1': {0, 1, 2, 3, 4, 5, 6, 8, 4104, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 4125, 38, 40, 43, 4142, 47, 4153, 4163, 80, 2129, 82, 4177, 84, 85, 4180, 4562, 4196, 2150, 4201, 2154, 4563, 114, 2165, 118, 2167, 4237, 4248, 4250, 4251, 160, 161, 162, 2214, 168, 169, 171, 176, 2226, 179, 181, 182, 183, 184, 4280, 186, 187, 188, 189, 190, 191, 4283, 4289, 194, 195, 4292, 197, 198, 199, 200, 201, 202, 203, 204, 205, 206, 207, 208, 209, 2258, 4315, 4316, 2269, 4319, 4324, 4116, 4568, 4333, 4336, 4342, 4343, 4344, 4366, 272, 273, 4368, 276, 277, 278, 279, 281, 283, 2334, 288, 289, 291, 292, 4388, 4389, 295, 4391, 297, 299, 4395, 4398, 303, 4402, 307, 308, 4403, 310, 312, 4408, 4409, 315, 316, 318, 323, 324, 4424, 333, 4429, 335, 4430, 4434, 4438, 4439, 344, 345, 347, 350, 355, 357, 358, 359, 4549, 361, 363, 364, 366, 4464, 369, 372, 373, 374, 375, 376, 4552, 378, 379, 380, 381, 382, 383, 384, 386, 388, 4485, 390, 391, 4487,

In [9]:
ground_truth_dict

{'Pertanyaan 1': {0,
  1,
  2,
  3,
  4,
  5,
  6,
  8,
  10,
  11,
  12,
  13,
  14,
  15,
  16,
  17,
  18,
  19,
  20,
  21,
  22,
  23,
  24,
  25,
  26,
  27,
  28,
  29,
  30,
  31,
  32,
  33,
  34,
  38,
  40,
  43,
  47,
  80,
  82,
  84,
  85,
  114,
  118,
  160,
  161,
  162,
  168,
  169,
  171,
  176,
  179,
  181,
  182,
  183,
  184,
  186,
  187,
  188,
  189,
  190,
  191,
  194,
  195,
  197,
  198,
  199,
  200,
  201,
  202,
  203,
  204,
  205,
  206,
  207,
  208,
  209,
  272,
  273,
  276,
  277,
  278,
  279,
  281,
  283,
  288,
  289,
  291,
  292,
  295,
  297,
  299,
  303,
  307,
  308,
  310,
  312,
  315,
  316,
  318,
  323,
  324,
  333,
  335,
  344,
  345,
  347,
  350,
  355,
  357,
  358,
  359,
  361,
  363,
  364,
  366,
  369,
  372,
  373,
  374,
  375,
  376,
  378,
  379,
  380,
  381,
  382,
  383,
  384,
  386,
  388,
  390,
  391,
  393,
  394,
  395,
  396,
  397,
  398,
  401,
  404,
  405,
  406,
  407,
  410,
  411,
  412,
  413,
  41

# Fungsi Evaluasi

In [9]:
def evaluate_retrieval(ground_truth_dict, query_id, retrieved_indices):
    relevant_indices = ground_truth_dict[query_id]
    retrieved_set = set(retrieved_indices)

    tp = len(retrieved_set & relevant_indices)  # True positives
    fp = len(retrieved_set - relevant_indices)  # False positives
    fn = len(relevant_indices - retrieved_set)  # False negatives

    precision = tp / (tp + fp) if tp + fp > 0 else 0
    recall = tp / (tp + fn) if tp + fn > 0 else 0

    return precision, recall

# Doc2Vec

In [13]:
from gensim.models.doc2vec import Doc2Vec, TaggedDocument
from sklearn.metrics.pairwise import cosine_similarity
import numpy as np
import pandas as pd


df['dokumen'] = df['dokumen'].astype(str)

# Tagging dokumen dengan indeksnya
tagged_docs = [TaggedDocument(words=row['dokumen'].split(), tags=[str(row['Index'])]) for _, row in df.iterrows()]


# Tagging dokumen dengan indeksnya
tagged_docs = [TaggedDocument(words=row['dokumen'].split(), tags=[str(row['Index'])]) for _, row in df.iterrows()]

# Inisialisasi dan pelatihan Doc2Vec
model = Doc2Vec(vector_size=50, min_count=1, epochs=20, workers=4)
model.build_vocab(tagged_docs)
model.train(tagged_docs, total_examples=model.corpus_count, epochs=model.epochs)

# Generate vektor untuk setiap dokumen
vectors = {str(row['Index']): model.infer_vector(row['dokumen'].split()) for _, row in df.iterrows()}

# Fungsi pencarian untuk mendapatkan top-k dokumen berdasarkan kesamaan kosinus
def retrieve_top_k(query, model, vectors, k):
    query_vector = model.infer_vector(query.split())
    similarities = {}

    for doc_id, doc_vector in vectors.items():
        similarity = cosine_similarity([query_vector], [doc_vector])[0][0]
        similarities[doc_id] = similarity

    # Urutkan berdasarkan kesamaan dalam urutan menurun
    sorted_indices = sorted(similarities, key=similarities.get, reverse=True)
    return sorted_indices[:k]

# Evaluasi untuk masing-masing top-k
results = []
for query_id, query in enumerate(df_pertanyaan, start=1):
    query_key = f"Pertanyaan {query_id}"
    for k in [5, 10, 20, 30, 40, 50, 60]:
        retrieved_indices = retrieve_top_k(query, model, vectors, k)
        precision, recall = evaluate_retrieval(ground_truth_dict, query_key, retrieved_indices)
        results.append({"query_id": query_key, "k": k, "precision": precision, "recall": recall})

# Tampilkan hasil evaluasi
results_df = pd.DataFrame(results)
print(results_df)


        query_id   k  precision  recall
0   Pertanyaan 1   5        0.0     0.0
1   Pertanyaan 1  10        0.0     0.0
2   Pertanyaan 1  20        0.0     0.0
3   Pertanyaan 1  30        0.0     0.0
4   Pertanyaan 1  40        0.0     0.0
5   Pertanyaan 1  50        0.0     0.0
6   Pertanyaan 1  60        0.0     0.0
7   Pertanyaan 2   5        0.0     0.0
8   Pertanyaan 2  10        0.0     0.0
9   Pertanyaan 2  20        0.0     0.0
10  Pertanyaan 2  30        0.0     0.0
11  Pertanyaan 2  40        0.0     0.0
12  Pertanyaan 2  50        0.0     0.0
13  Pertanyaan 2  60        0.0     0.0


# LSA

In [11]:
import pandas as pd
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.decomposition import TruncatedSVD
from sklearn.metrics.pairwise import cosine_similarity

# 1. TF-IDF Vectorization of the documents
tfidf_vectorizer = TfidfVectorizer()
doc_term_matrix = tfidf_vectorizer.fit_transform(df['processed_text'])

# 2. Apply Latent Semantic Analysis (LSA)
num_topics = 100  # Number of latent topics
lsa = TruncatedSVD(n_components=num_topics, random_state=42)
lsa_matrix = lsa.fit_transform(doc_term_matrix)

# Normalize the LSA matrix for cosine similarity
lsa_matrix_normalized = lsa_matrix / (np.linalg.norm(lsa_matrix, axis=1, keepdims=True) + 1e-9)

# 3. Process queries and transform them into the same LSA space
query_term_matrix = tfidf_vectorizer.transform(df_pertanyaan['processed_pertanyaan'])
query_lsa_matrix = lsa.transform(query_term_matrix)

# 4. Evaluate Retrieval for Top-k
def evaluate_top_k(ground_truth_dict, query_id, ranked_indices, k):
    relevant_indices = ground_truth_dict.get(query_id, set())
    retrieved_indices = set(ranked_indices[:k])

    tp = len(retrieved_indices & relevant_indices)  # True Positives
    precision = tp / len(retrieved_indices) if len(retrieved_indices) > 0 else 0
    recall = tp / len(relevant_indices) if len(relevant_indices) > 0 else 0

    return precision, recall

# Evaluate for multiple top-k values
top_k_values = [5, 10, 20, 30, 40, 50, 60]
evaluation_results = {}
average_results = {f"Top-{k}": {"Precision": 0, "Recall": 0} for k in top_k_values}


for i, query_vector in enumerate(query_lsa_matrix):
    query_id = f"Pertanyaan {i+1}"

    # Compute cosine similarity between query and document vectors
    similarities = cosine_similarity(query_vector.reshape(1, -1), lsa_matrix_normalized).flatten()

    # Rank documents based on similarity scores
    ranked_indices = similarities.argsort()[::-1]

    # Evaluate for each top-k value
    evaluation_results[query_id] = {}
    for k in top_k_values:
        precision, recall = evaluate_top_k(ground_truth_dict, query_id, ranked_indices, k)
        evaluation_results[query_id][f"Top-{k}"] = {
            "Precision": precision,
            "Recall": recall
        }
        average_results[f"Top-{k}"]["Precision"] += precision
        average_results[f"Top-{k}"]["Recall"] += recall

# Display evaluation results
for query_id, results in evaluation_results.items():
    print(f"\n{query_id}")
    for k, metrics in results.items():
        print(f"{k}: Precision = {metrics['Precision']:.2f}, Recall = {metrics['Recall']:.2f}")



Pertanyaan 1
Top-5: Precision = 0.80, Recall = 0.01
Top-10: Precision = 0.80, Recall = 0.01
Top-20: Precision = 0.70, Recall = 0.02
Top-30: Precision = 0.73, Recall = 0.04
Top-40: Precision = 0.70, Recall = 0.05
Top-50: Precision = 0.72, Recall = 0.06
Top-60: Precision = 0.70, Recall = 0.07

Pertanyaan 2
Top-5: Precision = 0.00, Recall = 0.00
Top-10: Precision = 0.10, Recall = 0.50
Top-20: Precision = 0.05, Recall = 0.50
Top-30: Precision = 0.03, Recall = 0.50
Top-40: Precision = 0.03, Recall = 0.50
Top-50: Precision = 0.02, Recall = 0.50
Top-60: Precision = 0.02, Recall = 0.50

Pertanyaan 3
Top-5: Precision = 1.00, Recall = 0.00
Top-10: Precision = 1.00, Recall = 0.00
Top-20: Precision = 0.95, Recall = 0.00
Top-30: Precision = 0.97, Recall = 0.01
Top-40: Precision = 0.95, Recall = 0.01
Top-50: Precision = 0.96, Recall = 0.01
Top-60: Precision = 0.97, Recall = 0.01

Pertanyaan 4
Top-5: Precision = 0.80, Recall = 0.00
Top-10: Precision = 0.60, Recall = 0.00
Top-20: Precision = 0.75, Re

In [12]:
# Compute averages
num_queries = len(query_lsa_matrix)
for k in top_k_values:
    average_results[f"Top-{k}"]["Precision"] /= num_queries
    average_results[f"Top-{k}"]["Recall"] /= num_queries

# Display average results
print("\nAverage Results:")
for k, metrics in average_results.items():
    print(f"{k}: Average Precision = {metrics['Precision']:.2f}, Average Recall = {metrics['Recall']:.2f}")



Average Results:
Top-5: Average Precision = 0.29, Average Recall = 0.09
Top-10: Average Precision = 0.24, Average Recall = 0.12
Top-20: Average Precision = 0.24, Average Recall = 0.15
Top-30: Average Precision = 0.23, Average Recall = 0.17
Top-40: Average Precision = 0.23, Average Recall = 0.20
Top-50: Average Precision = 0.22, Average Recall = 0.22
Top-60: Average Precision = 0.22, Average Recall = 0.24


# Word2Vec

In [13]:
import gensim
from gensim.models import Word2Vec
from sklearn.metrics import precision_score, recall_score
import numpy as np

# 1. Train Word2Vec model
def train_word2vec(docs):
    tokenized_docs = [doc.split() for doc in docs]  # Tokenize each document
    model = Word2Vec(sentences=tokenized_docs, vector_size=100, window=5, min_count=1, workers=4)
    return model

In [14]:
def get_doc_vector(doc, model):
    tokens = doc.split()
    vectors = [model.wv[token] for token in tokens if token in model.wv]
    if vectors:
        return np.mean(vectors, axis=0)
    else:
        return np.zeros(model.vector_size)

In [15]:
def retrieve_documents(query, model, df, top_k):
    query_vector = get_doc_vector(query, model)
    
    similarities = []
    for idx, doc in enumerate(df['processed_text']):
        doc_vector = get_doc_vector(doc, model)
        similarity = np.dot(query_vector, doc_vector) / (np.linalg.norm(query_vector) * np.linalg.norm(doc_vector) + 1e-10)  # Cosine similarity
        similarities.append((idx, similarity))

    similarities = sorted(similarities, key=lambda x: x[1], reverse=True)  # Sort by similarity
    return [idx for idx, _ in similarities[:top_k]]

In [16]:
word2vec_model = train_word2vec(df['processed_text'].tolist())


In [17]:
results = []
k_values = [5, 10, 20, 30, 40, 50, 60]

for query_id, query_text in df_pertanyaan[['pertanyaan', 'processed_pertanyaan']].iterrows():
    for k in k_values:
        retrieved = retrieve_documents(query_text['processed_pertanyaan'], word2vec_model, df, top_k=k)
        precision, recall = evaluate_retrieval(ground_truth_dict, f"Pertanyaan {query_id+1}", retrieved)
        results.append({"Query": query_text['pertanyaan'], "k": k, "Precision": precision, "Recall": recall})

# Convert results to DataFrame for better visualization
results_df = pd.DataFrame(results)


In [18]:
results_df.to_csv("retrieval_evaluation_results.csv", index=False)

In [19]:
file_path = 'retrieval_evaluation_results.csv'
df_results = pd.read_csv(file_path)

# Mengatur tampilan untuk menampilkan semua baris
pd.set_option('display.max_rows', None)

# Menampilkan seluruh isi DataFrame
print(df_results)

                                                 Query   k  Precision  \
0                                  Any dinner recipes?   5   0.800000   
1                                  Any dinner recipes?  10   0.600000   
2                                  Any dinner recipes?  20   0.400000   
3                                  Any dinner recipes?  30   0.400000   
4                                  Any dinner recipes?  40   0.450000   
5                                  Any dinner recipes?  50   0.380000   
6                                  Any dinner recipes?  60   0.383333   
7    Which recipes include both chicken and broccol...   5   0.000000   
8    Which recipes include both chicken and broccol...  10   0.000000   
9    Which recipes include both chicken and broccol...  20   0.000000   
10   Which recipes include both chicken and broccol...  30   0.000000   
11   Which recipes include both chicken and broccol...  40   0.000000   
12   Which recipes include both chicken and broccol

In [20]:
results_df = pd.read_csv("retrieval_evaluation_results.csv")

In [21]:
import pandas as pd

# Setelah loop untuk evaluasi retrieval
average_results = []

# Daftar nilai k yang ingin dievaluasi
k_values = [5, 10, 20, 30, 40, 50, 60]

# Hitung rata-rata Precision dan Recall untuk setiap k
for k in k_values:
    # Filter hasil untuk k tertentu
    filtered_results = results_df[results_df['k'] == k]
    
    # Hitung rata-rata Precision dan Recall
    avg_precision = filtered_results['Precision'].mean()
    avg_recall = filtered_results['Recall'].mean()
    
    # Simpan hasil rata-rata
    average_results.append({"k": k, "Average Precision": avg_precision, "Average Recall": avg_recall})

# Convert average_results ke DataFrame
average_results_df = pd.DataFrame(average_results)

# Tampilkan hasil rata-rata
print(average_results_df)

# Jika ingin menyimpan hasil rata-rata ke dalam file CSV
average_results_df.to_csv("average_retrieval_evaluation_results.csv", index=False)


    k  Average Precision  Average Recall
0   5           0.153333        0.014088
1  10           0.126667        0.016336
2  20           0.125833        0.046220
3  30           0.120556        0.049552
4  40           0.125417        0.056811
5  50           0.124333        0.063583
6  60           0.123333        0.068826


# BERT

In [22]:
import pandas as pd
from sentence_transformers import SentenceTransformer, util
import torch

# Load the pretrained BERT model (e.g., all-MiniLM-L6-v2 for semantic search)
model = SentenceTransformer('all-MiniLM-L6-v2')


c:\Users\acer\OneDrive\Documents\coolyeah\SEM 5\NLP\uas\.venv\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [23]:
#Encode processed_text (dokumen) dan pertanyaan
corpus_embeddings = model.encode(df['processed_text'].tolist(), convert_to_tensor=True)
query_embeddings = model.encode(df_pertanyaan['processed_pertanyaan'].tolist(), convert_to_tensor=True)

In [24]:
# Function to retrieve top-k documents for each query
def retrieve_top_k(query_embeddings, corpus_embeddings, top_k):
    results = []
    for query_embedding in query_embeddings:
        # Compute cosine similarity
        similarities = util.pytorch_cos_sim(query_embedding, corpus_embeddings).squeeze()
        
        # Retrieve top-k indices based on similarity
        top_k_indices = torch.topk(similarities, top_k).indices.tolist()
        results.append(top_k_indices)
    return results



In [27]:
# Evaluate for different top-k values
top_k_values = [5, 10, 20, 30, 40, 50, 60]
evaluation_results = {}
for top_k in top_k_values:
    # Retrieve top-k results
    top_k_results = retrieve_top_k(query_embeddings, corpus_embeddings, top_k)

    # Evaluate precision and recall for each query
    precision_list = []
    recall_list = []

    for i, retrieved_indices in enumerate(top_k_results):
        # Get ground truth for the current query
        query_key = f"Pertanyaan {i+1}"
        if query_key in ground_truth_dict:
            precision, recall = evaluate_retrieval(ground_truth_dict, query_key, retrieved_indices)
            precision_list.append(precision)
            recall_list.append(recall)

    # Average precision and recall for all queries
    avg_precision = sum(precision_list) / len(precision_list) if precision_list else 0
    avg_recall = sum(recall_list) / len(recall_list) if recall_list else 0

    evaluation_results[f"Top-{top_k}"] = (avg_precision, avg_recall)

    # Display evaluation results
print("Evaluation Results:")
for k, (precision, recall) in evaluation_results.items():
    print(f"{k}: Precision = {precision:.4f}, Recall = {recall:.4f}")



Evaluation Results:
Top-5: Precision = 0.3000, Recall = 0.0994
Top-10: Precision = 0.2850, Recall = 0.1347
Top-20: Precision = 0.2600, Recall = 0.1671
Top-30: Precision = 0.2506, Recall = 0.1862
Top-40: Precision = 0.2346, Recall = 0.2024
Top-50: Precision = 0.2290, Recall = 0.2195
Top-60: Precision = 0.2197, Recall = 0.2330


## MPNet

In [28]:
from transformers import MPNetTokenizer, MPNetModel
from sklearn.metrics.pairwise import cosine_similarity
import numpy as np

# Memuat tokenizer dan model MPNet
tokenizer = MPNetTokenizer.from_pretrained('microsoft/mpnet-base')
model = MPNetModel.from_pretrained('microsoft/mpnet-base')

Some weights of MPNetModel were not initialized from the model checkpoint at microsoft/mpnet-base and are newly initialized: ['mpnet.pooler.dense.bias', 'mpnet.pooler.dense.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [29]:
def get_embeddings(texts, batch_size=16):
    all_embeddings = []
    for i in range(0, len(texts), batch_size):
        batch = texts[i:i+batch_size]
        inputs = tokenizer(batch, padding=True, truncation=True, return_tensors='pt')
        with torch.no_grad():
            outputs = model(**inputs)
        embeddings = outputs.last_hidden_state.mean(dim=1)  # Mengambil rata-rata
        all_embeddings.append(embeddings.numpy())
    return np.vstack(all_embeddings)


In [31]:

import torch


In [32]:
# Mendapatkan embedding dari dokumen dan pertanyaan
document_embeddings = get_embeddings(df['processed_text'].tolist())
query_embeddings = get_embeddings(df_pertanyaan['processed_pertanyaan'].tolist())

# Fungsi untuk mencari dokumen relevan berdasarkan cosine similarity
def get_top_k_documents(query_embedding, document_embeddings, k):
    similarities = cosine_similarity(query_embedding.reshape(1, -1), document_embeddings)
    sorted_indices = np.argsort(similarities[0])[::-1]  # Urutkan berdasarkan kesamaan terbesar
    return sorted_indices[:k]

In [35]:
results = []

for query_id, query_embedding in enumerate(query_embeddings):
    for k in [5, 10, 20, 30, 40, 50, 60]:
        top_k_indices = get_top_k_documents(query_embedding, document_embeddings, k)
        precision, recall = evaluate_retrieval(ground_truth_dict, f"Pertanyaan {query_id + 1}", top_k_indices)
        results.append({
            'query_id': query_id + 1,
            'k': k,
            'precision': precision,
            'recall': recall
        })

# Menyimpan hasil evaluasi dalam DataFrame
evaluation_df = pd.DataFrame(results)

# Menampilkan hasil evaluasi
print(evaluation_df)

     query_id   k  precision    recall
0           1   5   0.000000  0.000000
1           1  10   0.000000  0.000000
2           1  20   0.000000  0.000000
3           1  30   0.000000  0.000000
4           1  40   0.000000  0.000000
..        ...  ..        ...       ...
415        60  20   0.050000  0.004762
416        60  30   0.033333  0.004762
417        60  40   0.025000  0.004762
418        60  50   0.020000  0.004762
419        60  60   0.016667  0.004762

[420 rows x 4 columns]


In [39]:
import pandas as pd

# Setelah loop untuk evaluasi retrieval
average_results = []
k_values = [5, 10, 20, 30, 40, 50, 60]

for k in k_values:
    # Filter hasil untuk k tertentu
    filtered_results = evaluation_df[evaluation_df['k'] == k]
    
    # Hitung rata-rata Precision dan Recall
    avg_precision = filtered_results['precision'].mean()
    avg_recall = filtered_results['recall'].mean()
    
    # Simpan hasil rata-rata
    average_results.append({"k": k, "Average Precision": avg_precision, "Average Recall": avg_recall})

# Convert average_results ke DataFrame
average_results_df = pd.DataFrame(average_results)

# Tampilkan hasil rata-rata
print(average_results_df)

# Jika ingin menyimpan hasil rata-rata ke dalam file CSV
average_results_df.to_csv("average_retrieval_evaluation_results.csv", index=False)


    k  Average Precision  Average Recall
0   5           0.120000        0.010875
1  10           0.120000        0.023112
2  20           0.106667        0.029751
3  30           0.105000        0.041545
4  40           0.102500        0.045585
5  50           0.101000        0.052697
6  60           0.100000        0.055437


: 

In [36]:
evaluation_df

query_id   k  precision    recall
0           1   5   0.000000  0.000000
1           1  10   0.000000  0.000000
2           1  20   0.000000  0.000000
3           1  30   0.000000  0.000000
4           1  40   0.000000  0.000000
..        ...  ..        ...       ...
415        60  20   0.050000  0.004762
416        60  30   0.033333  0.004762
417        60  40   0.025000  0.004762
418        60  50   0.020000  0.004762
419        60  60   0.016667  0.004762

[420 rows x 4 columns]

In [8]:
# # Fungsi Calculate Metrics
# def calculate_metrics(results_dict, ground_truth_dict):
#     precision_list = []
#     recall_list = []

#     for query, group in results_dict.items():
#         true_positives = 0
#         false_positives = 0
#         ground_truth = ground_truth_dict[query]

#         # Ambil daftar indeks dari hasil yang di-retrieve
#         retrieved_docs = set(group['Index'].tolist())  # Harus berasal dari kolom Index

#         correct_products = []
#         incorrect_products = []

#         for doc in retrieved_docs:
#             if doc in ground_truth:
#                 true_positives += 1
#                 correct_products.append(doc)
#             else:
#                 false_positives += 1
#                 incorrect_products.append(doc)

#         false_negatives = len(ground_truth) - true_positives

#         precision = true_positives / (true_positives + false_positives) if (true_positives + false_positives) > 0 else 0
#         recall = true_positives / (true_positives + false_negatives) if (true_positives + false_negatives) > 0 else 0

#         precision_list.append(precision)
#         recall_list.append(recall)

#         # Identifikasi dokumen yang hilang
#         missing_products = ground_truth - retrieved_docs

#         print(f"\nEvaluating {query}:")
#         print("Correct Indices:", correct_products)
#         print("Incorrect Indices:", incorrect_products)
#         print("Missing Indices:", list(missing_products))

#     avg_precision = sum(precision_list) / len(precision_list) if precision_list else 0
#     avg_recall = sum(recall_list) / len(recall_list) if recall_list else 0

#     print("\nMetrik Evaluasi:")
#     print(f"Rata-rata Presisi: {avg_precision:.3f}")
#     print(f"Rata-rata Recall: {avg_recall:.3f}")

In [9]:
result.head() #dataset
gt.head(10)

q1      q2  q3    q4     q5      q6     q7     q8    q9    q10  ...  \
0   0.0     4.0   0   0.0  291.0   343.0   17.0  210.0   4.0  210.0  ...   
1   1.0  3234.0   1   2.0  347.0   449.0  292.0  211.0   7.0  211.0  ...   
2   2.0     NaN   2   3.0  404.0   477.0  295.0  212.0  10.0  215.0  ...   
3   3.0     NaN   4   5.0  429.0   759.0  350.0  214.0  24.0  219.0  ...   
4   4.0     NaN   5   7.0  433.0   864.0  401.0  215.0  28.0  227.0  ...   
5   5.0     NaN   6   8.0  597.0   913.0  421.0  216.0  29.0  229.0  ...   
6   6.0     NaN   8   9.0  610.0   976.0  434.0  217.0  30.0  268.0  ...   
7   8.0     NaN   9  12.0  684.0   997.0  475.0  218.0  34.0  821.0  ...   
8  10.0     NaN  10  13.0  733.0  1003.0  479.0  219.0  37.0  822.0  ...   
9  11.0     NaN  11  17.0  734.0  1013.0  572.0  220.0  40.0  826.0  ...   

      q51    q52    q53    q54   q55    q56    q57    q58   q59    q60  
0  1098.0   60.0    4.0   49.0   0.0    4.0   17.0  229.0   4.0   50.0  
1  3077.0   61.0    8.0   55.0   1.0   27.0  286.0  233.0  10.0   51.0  
2  4219.0   73.0   14.0   57.0   2.0   97.0  292.0  252.0  12.0  120.0  
3     NaN  239.0   30.0   58.0   4.0  367.0  295.0  521.0  19.0  193.0  
4     NaN  243.0   32.0  296.0   5.0  459.0  334.0  522.0  22.0  222.0  
5     NaN  244.0  108.0  330.0   6.0  567.0  342.0  526.0  24.0  242.0  
6     NaN  362.0  123.0  365.0   8.0  577.0  350.0  628.0  34.0  250.0  
7     NaN  526.0  124.0  419.0   9.0  750.0  401.0  642.0  35.0  260.0  
8     NaN  538.0  218.0  447.0  10.0  788.0  421.0  644.0  37.0  266.0  
9     NaN  544.0  219.0  625.0  12.0  865.0  434.0  653.0  41.0  284.0  

[10 rows x 60 columns]

In [10]:
# Apply preprocessing to the 'dokumen' column
df['processed_text'] = df['dokumen'].apply(preprocess_text)

# Debugging: Check if 'processed_text' column exists
print(df.columns)  # Check the columns in the DataFrame
print(df[['Index', 'Headline', 'processed_text']].head())  # Preview the data

Index(['Index', 'Headline', 'Author Name', 'Details', 'Description',
       'Infomation', 'Nutrition', 'Serving', 'Rating', 'Rating Count',
       'Category', 'Cuisine', 'Ingredients', 'Instruction', 'dokumen',
       'processed_text'],
      dtype='object')
   Index                                           Headline  \
0      0  Eva Longoria’s 5-Ingredient Loaded Sweet Potatoes   
1      1  French Onion Cabbage Soup Is a Fun Twist on th...   
2      2   Making Cheesy Cabbage Gratin Is Worth the Effort   
3      3  Pumpkin-Summer Squash Ravioli with Brown Butte...   
4      4  This Orange Chicken &amp; Broccoli Skillet Is ...   

                                      processed_text  
0  eva longorias 5ingredient loaded sweet potatoe...  
1  french onion cabbage soup is a fun twist on th...  
2  making cheesy cabbage gratin is worth the effo...  
3  pumpkinsummer squash ravioli with brown butter...  
4  this orange chicken & amp broccoli skillet is ...  


# LSI

# Ontology Based

In [36]:
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.feature_extraction.text import TfidfVectorizer
from nltk.corpus import wordnet
import nltk

# Pastikan resource NLTK sudah diunduh
nltk.download('wordnet')
nltk.download('omw-1.4')

# Fungsi untuk mendapatkan sinonim dari WordNet
def get_synonyms(word):
    synonyms = set()
    for syn in wordnet.synsets(word):
        for lemma in syn.lemmas():
            synonyms.add(lemma.name().replace('_', ' '))
    return list(synonyms)

# Fungsi untuk ekspansi kueri menggunakan WordNet
def expand_query_with_wordnet(query):
    expanded_query = query
    for word in query.split():
        synonyms = get_synonyms(word)
        expanded_query += " " + " ".join(synonyms)
    return expanded_query

# Preprocess kueri dengan ekspansi menggunakan WordNet
df_pertanyaan['expanded_query'] = df_pertanyaan['processed_pertanyaan'].apply(expand_query_with_wordnet)

# Vectorize dokumen dan kueri
vectorizer = TfidfVectorizer()

document_vectors = vectorizer.fit_transform(df['processed_text'])
query_vectors = vectorizer.transform(df_pertanyaan['expanded_query'])

# Retrieve Top K Dokumen
def retrieve_top_k_documents(query_vector, document_vectors, top_k):
    similarities = cosine_similarity(query_vector, document_vectors).flatten()
    top_k_indices = similarities.argsort()[-top_k:][::-1]
    return top_k_indices

# Evaluasi untuk Top K (5, 10, 20, 30, 40, 50, 60)
results = {}
averages = {top_k: {"Precision": 0, "Recall": 0} for top_k in [5, 10, 20, 30, 40, 50, 60]}
query_count = query_vectors.shape[0]  # Menggunakan shape untuk mendapatkan jumlah kueri

for query_id, query_vector in enumerate(query_vectors):
    query_key = f"Pertanyaan {query_id + 1}"
    results[query_key] = {}

    for top_k in [5, 10, 20, 30, 40, 50, 60]:
        retrieved_indices = retrieve_top_k_documents(query_vector, document_vectors, top_k)
        precision, recall = evaluate_retrieval(ground_truth_dict, query_key, retrieved_indices)
        results[query_key][f"Top {top_k}"] = {
            "Precision": precision,
            "Recall": recall
        }
        averages[top_k]["Precision"] += precision
        averages[top_k]["Recall"] += recall

# Hitung rata-rata untuk masing-masing Top K
for top_k in averages:
    averages[top_k]["Precision"] /= query_count
    averages[top_k]["Recall"] /= query_count

# Tampilkan Hasil Evaluasi
import pprint
pprint.pprint(results)
print("\nRata-rata untuk masing-masing Top K:")
pprint.pprint(averages)


[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\acer\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package omw-1.4 to
[nltk_data]     C:\Users\acer\AppData\Roaming\nltk_data...
[nltk_data]   Package omw-1.4 is already up-to-date!


{'Pertanyaan 1': {'Top 10': {'Precision': 0.9, 'Recall': 0.014975041597337771},
                  'Top 20': {'Precision': 0.95, 'Recall': 0.03161397670549085},
                  'Top 30': {'Precision': 0.8666666666666667,
                             'Recall': 0.04326123128119801},
                  'Top 40': {'Precision': 0.85, 'Recall': 0.056572379367720464},
                  'Top 5': {'Precision': 1.0, 'Recall': 0.008319467554076539},
                  'Top 50': {'Precision': 0.84, 'Recall': 0.06988352745424292},
                  'Top 60': {'Precision': 0.8333333333333334,
                             'Recall': 0.08319467554076539}},
 'Pertanyaan 10': {'Top 10': {'Precision': 0.7, 'Recall': 0.30434782608695654},
                   'Top 20': {'Precision': 0.65, 'Recall': 0.5652173913043478},
                   'Top 30': {'Precision': 0.5, 'Recall': 0.6521739130434783},
                   'Top 40': {'Precision': 0.475, 'Recall': 0.8260869565217391},
                   'Top 5': {'Pre

# Word Embedding

In [16]:
# import pandas as pd
# import numpy as np
# from gensim.models import KeyedVectors
# from nltk.tokenize import word_tokenize

In [17]:
# def get_embedding(text, model):
#     """Generate an average embedding for the given text."""
#     tokens = word_tokenize(text)
#     embeddings = [model[word] for word in tokens if word in model]
#     return np.mean(embeddings, axis=0) if embeddings else np.zeros(model.vector_size)

# def retrieve_documents(queries, df, model):
#     """Retrieve documents relevant to each query based on embeddings."""
#     results_dict = {}
    
#     # Generate embeddings for each document
#     df['embeddings'] = df['processed_text'].apply(lambda x: get_embedding(x, model))

#     for query in queries:
#         query_embedding = get_embedding(query, model)
#         df['similarity'] = df['embeddings'].apply(lambda x: np.dot(query_embedding, x) / (np.linalg.norm(query_embedding) * np.linalg.norm(x)) if np.any(x) else 0)
        
#         # Sort documents by similarity score
#         top_results = df.nlargest(10, 'similarity')  # Retrieve top 10 documents
#         results_dict[query] = top_results

#     return results_dict 

In [20]:
# model = KeyedVectors.load_word2vec_format('path/to/GoogleNews-vectors-negative300.bin', binary=True)


FileNotFoundError: [Errno 2] No such file or directory: 'path/to/GoogleNews-vectors-negative300.bin'

In [23]:
# import gzip
# import shutil

# with gzip.open('GoogleNews-vectors-negative300.bin.gz', 'rb') as f_in:
#     with open('GoogleNews-vectors-negative300.bin', 'wb') as f_out:
#         shutil.copyfileobj(f_in, f_out)


In [25]:
# # Make sure to load your Word2Vec model before this step
# model = KeyedVectors.load_word2vec_format('GoogleNews-vectors-negative300.bin', binary=True)

# queries = df_pertanyaan['processed_pertanyaan'].tolist()  # Get processed queries
# results_dict = retrieve_documents(queries, df, model)

# # Display results for a specific query
# for query, results in results_dict.items():
#     print(f"Results for query: {query}")
#     print(results[['Index', 'Headline', 'similarity']])

Results for query: any dinner recipes
      Index                               Headline  similarity
2165   2165                     Greek Salmon Salad    0.627039
3207   3207      Pork Wrap with Lime-Jalapeño Slaw    0.600516
3169   3169      Chicken, Quinoa &amp; Veggie Bowl    0.592627
4732   4732    Turkey Meatball &amp; Feta Lunchbox    0.589272
3167   3167            Loaded Chicken-Quinoa Salad    0.587376
383     383       Easy Chicken Enchilada Casserole    0.586069
3470   3470    Baked Parmesan Zucchini Curly Fries    0.585372
2945   2945       Chipotle Ranch Chicken Casserole    0.584934
4315   4315                 Chicken Tinga Tostadas    0.584132
770     770  Pasta Salad with Vinaigrette Lunchbox    0.582548
Results for query: which recipes include both chicken and broccoli as ingredients and have a mediterranean diet classification
      Index                                      Headline  similarity
2165   2165                            Greek Salmon Salad    0.797500
31

# BM25L

In [23]:
import numpy as np
import pandas as pd

class BM25L:
    def __init__(self, corpus, b=0.75, k1=1.5, delta=0.5):
        self.corpus = [doc.split() for doc in corpus]
        self.b = b
        self.k1 = k1
        self.delta = delta
        self.doc_lengths = np.array([len(doc) for doc in self.corpus])
        self.avg_doc_length = np.mean(self.doc_lengths)
        self.doc_freqs = self._compute_doc_frequencies()
        self.idf = self._compute_idf()

    def _compute_doc_frequencies(self):
        freqs = {}
        for doc in self.corpus:
            for term in set(doc):
                if term not in freqs:
                    freqs[term] = 0
                freqs[term] += 1
        return freqs

    def _compute_idf(self):
        total_docs = len(self.corpus)
        return {
            term: np.log((total_docs - freq + 0.5) / (freq + 0.5) + 1)
            for term, freq in self.doc_freqs.items()
        }

    def _score(self, query, doc, doc_length):
        score = 0
        for term in query:
            if term in self.doc_freqs:
                idf = self.idf[term]
                freq = doc.count(term)
                norm_len = (1 - self.b) + self.b * (doc_length / self.avg_doc_length)
                numerator = freq * (self.k1 + 1)
                denominator = freq + self.k1 * norm_len + self.delta
                score += idf * (numerator / denominator)
        return score

    def get_scores(self, query):
        query = query.split()
        scores = [
            self._score(query, doc, doc_length)
            for doc, doc_length in zip(self.corpus, self.doc_lengths)
        ]
        return np.array(scores)

# Fungsi untuk pencarian menggunakan BM25L
def bm25l_search(query, documents):
    bm25l = BM25L(documents)
    scores = bm25l.get_scores(query)
    return scores

# # Proses pencarian dengan BM25L
# results_dict_bm25l = {}

# for idx, row in df_pertanyaan.iterrows():
#     query = row['processed_pertanyaan']
#     documents = df['processed_text'].tolist()
#     bm25l_scores = bm25l_search(query, documents)
#     results = pd.DataFrame({
#         'Index': df["Index"],  # Menggunakan indeks dokumen
#         'Dokumen': documents,
#         'BM25L Score': bm25l_scores
#     })

#     results = results.sort_values(by='BM25L Score', ascending=False).head(20)
#     results['Query'] = row['pertanyaan']
#     results_dict_bm25l[f'Pertanyaan {idx + 1}'] = results

# # Menampilkan hasil
# for question, result in results_dict_bm25l.items():
#     print(question)
#     for i, row in result.iterrows():
#         print(f"Document {i + 1}:")
#         print(f"BM25L Score: {row['BM25L Score']:.4f}")
#         print(f"Index Dokumen: {row['Index']}")  # Menampilkan indeks dokumen
#         print(f"{row['Dokumen']}\n")
#     print("\n" + "=" * 50 + "\n")


In [24]:
# Evaluasi pencarian menggunakan BM25L
results_bm25l = []
k_values = [5, 10, 20, 30, 40, 50, 60]

# Melakukan iterasi untuk setiap kueri dalam df_pertanyaan
for query_id, query_text in df_pertanyaan[['pertanyaan', 'processed_pertanyaan']].iterrows():
    for k in k_values:
        # Mencari dokumen relevan dengan BM25L
        retrieved_scores = bm25l_search(query_text['processed_pertanyaan'], df['processed_text'])
        
        # Menyortir dokumen berdasarkan skor BM25L dan mengambil top k dokumen
        top_k_indices = np.argsort(retrieved_scores)[-k:][::-1]
        
        # Mendapatkan hasil evaluasi (precision, recall)
        precision, recall = evaluate_retrieval(ground_truth_dict, f"Pertanyaan {query_id+1}", top_k_indices)
        
        # Menyimpan hasil evaluasi
        results_bm25l.append({
            "Query": query_text['pertanyaan'],
            "k": k,
            "Precision": precision,
            "Recall": recall
        })

# Mengonversi hasil evaluasi ke dalam DataFrame untuk analisis lebih lanjut
df_results_bm25l = pd.DataFrame(results_bm25l)

# Menampilkan hasil evaluasi
print(df_results_bm25l)

                                                Query   k  Precision    Recall
0                                 Any dinner recipes?   5   0.800000  0.006656
1                                 Any dinner recipes?  10   0.800000  0.013311
2                                 Any dinner recipes?  20   0.850000  0.028286
3                                 Any dinner recipes?  30   0.866667  0.043261
4                                 Any dinner recipes?  40   0.850000  0.056572
..                                                ...  ..        ...       ...
415  Give me a diet dish that contains no vegetables.  20   0.000000  0.000000
416  Give me a diet dish that contains no vegetables.  30   0.000000  0.000000
417  Give me a diet dish that contains no vegetables.  40   0.000000  0.000000
418  Give me a diet dish that contains no vegetables.  50   0.000000  0.000000
419  Give me a diet dish that contains no vegetables.  60   0.016667  0.004762

[420 rows x 4 columns]


In [25]:
import pandas as pd

# Setelah loop untuk evaluasi retrieval
average_results = []
k_values = [5, 10, 20, 30, 40, 50, 60]

for k in k_values:
    # Filter hasil untuk k tertentu
    filtered_results = df_results_bm25l[df_results_bm25l['k'] == k]
    
    # Hitung rata-rata Precision dan Recall
    avg_precision = filtered_results['Precision'].mean()
    avg_recall = filtered_results['Recall'].mean()
    
    # Simpan hasil rata-rata
    average_results.append({"k": k, "Average Precision": avg_precision, "Average Recall": avg_recall})

# Convert average_results ke DataFrame
average_results_df = pd.DataFrame(average_results)

# Tampilkan hasil rata-rata
print(average_results_df)

# Jika ingin menyimpan hasil rata-rata ke dalam file CSV
average_results_df.to_csv("average_retrieval_evaluation_results.csv", index=False)


    k  Average Precision  Average Recall
0   5           0.380000        0.192579
1  10           0.335000        0.226147
2  20           0.291667        0.262813
3  30           0.280556        0.290483
4  40           0.275833        0.325330
5  50           0.267000        0.358157
6  60           0.255278        0.378884


In [ ]:
# results = []
# k_values = [5, 10, 20, 30, 40, 50, 60]

# for query_id, query_text in df_pertanyaan[['pertanyaan', 'processed_pertanyaan']].iterrows():
#     for k in k_values:
#         retrieved = retrieve_documents(query_text['processed_pertanyaan'], word2vec_model, df, top_k=k)
#         precision, recall = evaluate_retrieval(ground_truth_dict, f"Pertanyaan {query_id+1}", retrieved)
#         results.append({"Query": query_text['pertanyaan'], "k": k, "Precision": precision, "Recall": recall})


In [45]:
# calculate_metrics(results_dict_bm25l, ground_truth_dict)


Evaluating Pertanyaan 1:
Correct Indices: [3207, 3984, 786, 4504, 2214, 312, 3392, 4043, 4177, 3167, 3169, 372, 2165, 2937]
Incorrect Indices: [389, 782, 4756, 2095, 3163, 3316]
Missing Indices: [0, 1, 2, 3, 4, 5, 6, 8, 4104, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 4125, 38, 40, 43, 4142, 47, 4153, 4163, 80, 2129, 82, 84, 85, 4180, 4562, 4196, 2150, 4201, 2154, 4563, 114, 118, 2167, 4237, 4248, 4250, 4251, 160, 161, 162, 168, 169, 171, 176, 2226, 179, 181, 182, 183, 184, 4280, 186, 187, 188, 189, 190, 191, 4283, 4289, 194, 195, 4292, 197, 198, 199, 200, 201, 202, 203, 204, 205, 206, 207, 208, 209, 2258, 4315, 4316, 2269, 4319, 4324, 4116, 4568, 4333, 4336, 4342, 4343, 4344, 4366, 272, 273, 4368, 276, 277, 278, 279, 281, 283, 2334, 288, 289, 291, 292, 4388, 4389, 295, 4391, 297, 299, 4395, 4398, 303, 4402, 307, 308, 4403, 310, 4408, 4409, 315, 316, 318, 323, 324, 4424, 333, 4429, 335, 4430, 4434, 4438, 4439, 344, 345, 347, 350

# Hybrid

## Ontology + BM25L

In [54]:
from nltk.corpus import wordnet as wn
import pandas as pd
import numpy as np

# Step 1: Define the ontology-based search function
def ontology_search(query):
    # Replace this with actual ontology querying logic
    synonyms = get_synonyms(query)  # You can use the same get_synonyms function
    return list(synonyms)

# Step 2: Modify the BM25L search to include ontology search
def hybrid_search(query, documents):
    # Get ontology-based results
    ontology_results = ontology_search(query)

    # Use BM25L for document scoring
    bm25l = BM25L(documents)
    bm25l_scores = bm25l.get_scores(query)

    # Combine results
    combined_results = []
    for term in ontology_results:
        if term in documents:
            idx = documents.index(term)
            combined_results.append((idx, bm25l_scores[idx] + 1))  # Boosting scores from ontology

    # Add BM25L scores for documents
    for idx, score in enumerate(bm25l_scores):
        combined_results.append((idx, score))

    # Remove duplicates and sort by score
    combined_results = list(set(combined_results))
    combined_results.sort(key=lambda x: x[1], reverse=True)

    return combined_results

# Step 3: Process queries with the hybrid search
results_dict_hybrid = {}

for idx, row in df_pertanyaan.iterrows():
    query = row['processed_pertanyaan']
    documents = df['processed_text'].tolist()
    
    hybrid_scores = hybrid_search(query, documents)
    
    results = pd.DataFrame({
        'Index': df["Index"].tolist(),
        'Dokumen': documents,
        'Hybrid Score': [score for _, score in hybrid_scores]
    })

    results = results.sort_values(by='Hybrid Score', ascending=False).head(20)
    results['Query'] = row['pertanyaan']
    results_dict_hybrid[f'Pertanyaan {idx + 1}'] = results

# Step 4: Display the results
for question, result in results_dict_hybrid.items():
    print(question)
    for i, row in result.iterrows():
        print(f"Document {i + 1}:")
        print(f"Hybrid Score: {row['Hybrid Score']:.4f}")
        print(f"Index Dokumen: {row['Index']}")
        print(f"{row['Dokumen']}\n")
    print("\n" + "=" * 50 + "\n")
    
from nltk.corpus import wordnet as wn
import pandas as pd
import numpy as np

# Step 1: Define the ontology-based search function
def ontology_search(query):
    # Replace this with actual ontology querying logic
    synonyms = get_synonyms(query)  # You can use the same get_synonyms function
    return list(synonyms)

# Step 2: Modify the BM25L search to include ontology search
def hybrid_search(query, documents):
    # Get ontology-based results
    ontology_results = ontology_search(query)

    # Use BM25L for document scoring
    bm25l = BM25L(documents)
    bm25l_scores = bm25l.get_scores(query)

    # Combine results
    combined_results = []
    for term in ontology_results:
        if term in documents:
            idx = documents.index(term)
            combined_results.append((idx, bm25l_scores[idx] + 1))  # Boosting scores from ontology

    # Add BM25L scores for documents
    for idx, score in enumerate(bm25l_scores):
        combined_results.append((idx, score))

    # Remove duplicates and sort by score
    combined_results = list(set(combined_results))
    combined_results.sort(key=lambda x: x[1], reverse=True)

    return combined_results

# Step 3: Process queries with the hybrid search
results_dict_hybrid = {}

for idx, row in df_pertanyaan.iterrows():
    query = row['processed_pertanyaan']
    documents = df['processed_text'].tolist()
    
    hybrid_scores = hybrid_search(query, documents)
    
    results = pd.DataFrame({
        'Index': df["Index"].tolist(),
        'Dokumen': documents,
        'Hybrid Score': [score for _, score in hybrid_scores]
    })

    results = results.sort_values(by='Hybrid Score', ascending=False).head(20)
    results['Query'] = row['pertanyaan']
    results_dict_hybrid[f'Pertanyaan {idx + 1}'] = results

# Step 4: Display the results
for question, result in results_dict_hybrid.items():
    print(question)
    for i, row in result.iterrows():
        print(f"Document {i + 1}:")
        print(f"Hybrid Score: {row['Hybrid Score']:.4f}")
        print(f"Index Dokumen: {row['Index']}")
        print(f"{row['Dokumen']}\n")
    print("\n" + "=" * 50 + "\n")

Pertanyaan 1
Document 1:
Hybrid Score: 8.8549
Index Dokumen: 0
eva longorias 5ingredient loaded sweet potatoes eva longoria active time 20 mins total time 1 hr 20 mins servings 4 eva longorias loaded sweet potatoes from her cookbook my mexican kitchen calls for five ingredients and makes a delicious main [ no added sugar sesamefree nutfree soyfree eggfree glutenfree ] total carbohydrate 34g dietary fiber 5g total sugars 9g protein 12g total fat 41g saturated fat 20g cholesterol 96mg vitamin a 1408g vitamin c 10mg vitamin d 0g vitamin e 1mg folate 25g vitamin k 21g sodium 603mg calcium 191mg iron 1mg magnesium 53mg potassium 724mg zinc 2mg vitamin b12 0g omega 3 0g servings per recipe 4 serving size 1 potato calories 549 50 1 [ dinner ] [ american ] [ 4 large sweet potatoes 6 slices bacon 4 tablespoons unsalted butter 2 scallions white and lightgreen parts only thinly sliced 1/2 cup freshly grated quesillo oaxaca cheese monterey jack mozzarella or queso fresco 1/2 cup mexican crema ] [ 

In [49]:
calculate_metrics(results_dict_hybrid, ground_truth_dict)


Evaluating Pertanyaan 1:
Correct Indices: [0, 1, 2, 3, 4, 5, 6, 8, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19]
Incorrect Indices: [7, 9]
Missing Indices: [4104, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 4125, 38, 40, 43, 4142, 47, 4153, 4163, 80, 2129, 82, 4177, 84, 85, 4180, 4562, 4196, 2150, 4201, 2154, 4563, 114, 2165, 118, 2167, 4237, 4248, 4250, 4251, 160, 161, 162, 2214, 168, 169, 171, 176, 2226, 179, 181, 182, 183, 184, 4280, 186, 187, 188, 189, 190, 191, 4283, 4289, 194, 195, 4292, 197, 198, 199, 200, 201, 202, 203, 204, 205, 206, 207, 208, 209, 2258, 4315, 4316, 2269, 4319, 4324, 4116, 4568, 4333, 4336, 4342, 4343, 4344, 4366, 272, 273, 4368, 276, 277, 278, 279, 281, 283, 2334, 288, 289, 291, 292, 4388, 4389, 295, 4391, 297, 299, 4395, 4398, 303, 4402, 307, 308, 4403, 310, 312, 4408, 4409, 315, 316, 318, 323, 324, 4424, 333, 4429, 335, 4430, 4434, 4438, 4439, 344, 345, 347, 350, 355, 357, 358, 359, 4549, 361, 363, 364, 366, 4464, 369, 372, 373, 374, 375, 376, 45

## Hybrid 

Word2Vec + BM25L

In [55]:
import numpy as np
from gensim.models import Word2Vec
from sklearn.metrics.pairwise import cosine_similarity

# Load Word2Vec model (gunakan model pre-trained atau latih sendiri jika belum ada)
# Misalnya model pre-trained: Google News atau model lain yang sesuai dengan corpus Anda
# Untuk contoh ini, kita latih Word2Vec sederhana dari corpus

word2vec_model = Word2Vec(df['processed_text'].str.split(), vector_size=100, window=5, min_count=1, workers=4)

def get_document_vector(doc, model):
    tokens = doc.split()
    word_vectors = [model.wv[word] for word in tokens if word in model.wv]
    if len(word_vectors) == 0:
        return np.zeros(model.vector_size)
    return np.mean(word_vectors, axis=0)

# Hybrid IR function
def hybrid_search(query, documents, bm25_weight=0.5):
    # BM25L scoring
    bm25l = BM25L(documents)
    bm25_scores = bm25l.get_scores(query)

    # Word2Vec similarity
    query_vector = get_document_vector(query, word2vec_model)
    doc_vectors = np.array([get_document_vector(doc, word2vec_model) for doc in documents])
    w2v_scores = cosine_similarity([query_vector], doc_vectors)[0]

    # Normalize scores
    bm25_scores = (bm25_scores - np.min(bm25_scores)) / (np.max(bm25_scores) - np.min(bm25_scores))
    w2v_scores = (w2v_scores - np.min(w2v_scores)) / (np.max(w2v_scores) - np.min(w2v_scores))

    # Combine scores
    hybrid_scores = bm25_weight * bm25_scores + (1 - bm25_weight) * w2v_scores
    return hybrid_scores

# Evaluasi pada top-k hasil
def evaluate_topk(ground_truth_dict, query_key, hybrid_scores, k_values):
    sorted_indices = np.argsort(hybrid_scores)[::-1]  # Urutkan berdasarkan skor (descending)

    results = []
    for k in k_values:
        top_k_indices = sorted_indices[:k]
        precision, recall = evaluate_retrieval(ground_truth_dict, query_key, top_k_indices)
        results.append({
            'k': k,
            'precision': precision,
            'recall': recall
        })

    return results

# Evaluasi semua query
results_hybrid = []
k_values = [5, 10, 20, 30, 40, 50, 60]

for query_id, query_text in df_pertanyaan[['pertanyaan', 'processed_pertanyaan']].iterrows():
    query_key = f"Pertanyaan {query_id + 1}"
    hybrid_scores = hybrid_search(query_text['processed_pertanyaan'], documents)

    evaluation_results = evaluate_topk(ground_truth_dict, query_key, hybrid_scores, k_values)
    for result in evaluation_results:
        results_hybrid.append({
            'Query': query_text['pertanyaan'],
            'k': result['k'],
            'Precision': result['precision'],
            'Recall': result['recall']
        })

# Konversi hasil evaluasi ke DataFrame untuk analisis lebih lanjut
df_results_hybrid = pd.DataFrame(results_hybrid)

# Menampilkan hasil evaluasi
print(df_results_hybrid)


                                                Query   k  Precision    Recall
0                                 Any dinner recipes?   5   0.200000  0.001664
1                                 Any dinner recipes?  10   0.200000  0.003328
2                                 Any dinner recipes?  20   0.200000  0.006656
3                                 Any dinner recipes?  30   0.266667  0.013311
4                                 Any dinner recipes?  40   0.225000  0.014975
..                                                ...  ..        ...       ...
415  Give me a diet dish that contains no vegetables.  20   0.000000  0.000000
416  Give me a diet dish that contains no vegetables.  30   0.000000  0.000000
417  Give me a diet dish that contains no vegetables.  40   0.000000  0.000000
418  Give me a diet dish that contains no vegetables.  50   0.000000  0.000000
419  Give me a diet dish that contains no vegetables.  60   0.000000  0.000000

[420 rows x 4 columns]


In [56]:
import pandas as pd

average_results = []

k_values = [5, 10, 20, 30, 40, 50, 60]
for k in k_values:
    # Filter hasil untuk k tertentu
    filtered_results = df_results_hybrid[df_results_hybrid['k'] == k]
    
    # Hitung rata-rata Precision dan Recall
    avg_precision = filtered_results['Precision'].mean()
    avg_recall = filtered_results['Recall'].mean()
    
    # Simpan hasil rata-rata
    average_results.append({"k": k, "Average Precision": avg_precision, "Average Recall": avg_recall})

# Convert average_results ke DataFrame
average_results_df = pd.DataFrame(average_results)

# Tampilkan hasil rata-rata
print(average_results_df)

# Jika ingin menyimpan hasil rata-rata ke dalam file CSV
average_results_df.to_csv("average_retrieval_evaluation_results.csv", index=False)


    k  Average Precision  Average Recall
0   5           0.086667        0.000759
1  10           0.088333        0.011137
2  20           0.089167        0.032767
3  30           0.093333        0.037293
4  40           0.092500        0.049156
5  50           0.093000        0.052365
6  60           0.095556        0.059361


## BM25L + BERT

In [28]:
import pandas as pd
import numpy as np
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity
from rank_bm25 import BM25L
from sentence_transformers import SentenceTransformer

# Preprocessing data
# df: Dataframe containing processed documents
# df_pertanyaan: Dataframe containing processed queries
# ground_truth_dict: Dictionary of ground truth relevance

# 1. TF-IDF Vectorization of the documents
tfidf_vectorizer = TfidfVectorizer()
doc_term_matrix = tfidf_vectorizer.fit_transform(df['processed_text'])

# 2. BERT Embeddings for documents
bert_model = SentenceTransformer('all-MiniLM-L6-v2')
document_embeddings = bert_model.encode(df['processed_text'].tolist(), convert_to_tensor=True)

# 3. BM25L Initialization
documents = df['processed_text'].tolist()
documents_tokenized = [doc.split() for doc in documents]  # Tokenize documents
bm25l = BM25L(documents_tokenized)

# Generate BERT embeddings for queries
query_embeddings = bert_model.encode(df_pertanyaan['processed_pertanyaan'].tolist(), convert_to_tensor=True)

# RRF Hybrid Scoring Function
def rrf_hybrid_score(query_index, k=60):
    # BM25L scores
    query_tokens = df_pertanyaan['processed_pertanyaan'][query_index].split()
    bm25_scores = bm25l.get_scores(query_tokens)

    # BERT cosine similarity scores
    bert_scores = cosine_similarity(
        query_embeddings[query_index].reshape(1, -1), document_embeddings.cpu().numpy()
    ).flatten()

    # Compute RRF scores for both methods
    rrf_bm25 = 1 / (np.argsort(np.argsort(-bm25_scores)) + 1 + k)
    rrf_bert = 1 / (np.argsort(np.argsort(-bert_scores)) + 1 + k)

    # Combine RRF scores
    rrf_scores = rrf_bm25 + rrf_bert

    return rrf_scores

# Evaluate Retrieval for Top-k
def evaluate_top_k(ground_truth_dict, query_id, ranked_indices, k):
    relevant_indices = ground_truth_dict.get(query_id, set())
    retrieved_indices = set(ranked_indices[:k])

    tp = len(retrieved_indices & relevant_indices)  # True Positives
    precision = tp / len(retrieved_indices) if len(retrieved_indices) > 0 else 0
    recall = tp / len(relevant_indices) if len(relevant_indices) > 0 else 0

    return precision, recall

# Evaluate for multiple top-k values
top_k_values = [5, 10, 20, 30, 40, 50, 60]
evaluation_results = {}

for i in range(len(df_pertanyaan)):
    query_id = f"Pertanyaan {i+1}"

    # Compute RRF hybrid scores
    rrf_scores = rrf_hybrid_score(i)

    # Rank documents based on RRF hybrid scores
    ranked_indices = np.argsort(rrf_scores)[::-1]

    # Evaluate for each top-k value
    evaluation_results[query_id] = {}
    for k in top_k_values:
        precision, recall = evaluate_top_k(ground_truth_dict, query_id, ranked_indices, k)
        evaluation_results[query_id][f"Top-{k}"] = {
            "Precision": precision,
            "Recall": recall
        }

# Calculate and display average Precision and Recall for each top-k
average_results = {f"Top-{k}": {"Precision": 0, "Recall": 0} for k in top_k_values}

for query_id, results in evaluation_results.items():
    for k in top_k_values:
        average_results[f"Top-{k}"]["Precision"] += results[f"Top-{k}"]["Precision"]
        average_results[f"Top-{k}"]["Recall"] += results[f"Top-{k}"]["Recall"]

for k in top_k_values:
    average_results[f"Top-{k}"]["Precision"] /= len(df_pertanyaan)
    average_results[f"Top-{k}"]["Recall"] /= len(df_pertanyaan)

# Display evaluation results for each query
for query_id, results in evaluation_results.items():
    print(f"\n{query_id}")
    for k, metrics in results.items():
        print(f"{k}: Precision = {metrics['Precision']:.2f}, Recall = {metrics['Recall']:.2f}")

# Display average results
print("\nAverage Results:")
for k, metrics in average_results.items():
    print(f"{k}: Precision = {metrics['Precision']:.2f}, Recall = {metrics['Recall']:.2f}")


c:\Users\acer\OneDrive\Documents\coolyeah\SEM 5\NLP\uas\.venv\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm



Pertanyaan 1
Top-5: Precision = 1.00, Recall = 0.01
Top-10: Precision = 0.90, Recall = 0.01
Top-20: Precision = 0.90, Recall = 0.03
Top-30: Precision = 0.87, Recall = 0.04
Top-40: Precision = 0.90, Recall = 0.06
Top-50: Precision = 0.88, Recall = 0.07
Top-60: Precision = 0.87, Recall = 0.09

Pertanyaan 2
Top-5: Precision = 0.20, Recall = 0.50
Top-10: Precision = 0.10, Recall = 0.50
Top-20: Precision = 0.05, Recall = 0.50
Top-30: Precision = 0.07, Recall = 1.00
Top-40: Precision = 0.05, Recall = 1.00
Top-50: Precision = 0.04, Recall = 1.00
Top-60: Precision = 0.03, Recall = 1.00

Pertanyaan 3
Top-5: Precision = 0.60, Recall = 0.00
Top-10: Precision = 0.80, Recall = 0.00
Top-20: Precision = 0.75, Recall = 0.00
Top-30: Precision = 0.80, Recall = 0.01
Top-40: Precision = 0.80, Recall = 0.01
Top-50: Precision = 0.82, Recall = 0.01
Top-60: Precision = 0.85, Recall = 0.01

Pertanyaan 4
Top-5: Precision = 1.00, Recall = 0.00
Top-10: Precision = 1.00, Recall = 0.01
Top-20: Precision = 0.85, Re

## Word2Vec + BM25L

In [27]:
import pandas as pd
import numpy as np
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.decomposition import TruncatedSVD
from sklearn.metrics.pairwise import cosine_similarity
from rank_bm25 import BM25L

# Preprocessing data
# df: Dataframe containing processed documents
# df_pertanyaan: Dataframe containing processed queries
# ground_truth_dict: Dictionary of ground truth relevance

# 1. TF-IDF Vectorization of the documents
tfidf_vectorizer = TfidfVectorizer()
doc_term_matrix = tfidf_vectorizer.fit_transform(df['processed_text'])

# 2. Apply Latent Semantic Analysis (LSA)
num_topics = 100  # Number of latent topics
lsa = TruncatedSVD(n_components=num_topics, random_state=42)
lsa_matrix = lsa.fit_transform(doc_term_matrix)

# Normalize the LSA matrix for cosine similarity
lsa_matrix_normalized = lsa_matrix / (np.linalg.norm(lsa_matrix, axis=1, keepdims=True) + 1e-9)

# 3. BM25L Initialization
documents = df['processed_text'].tolist()
documents_tokenized = [doc.split() for doc in documents]  # Tokenize documents
bm25l = BM25L(documents_tokenized)

# Process queries and transform them into the same LSA space
query_term_matrix = tfidf_vectorizer.transform(df_pertanyaan['processed_pertanyaan'])
query_lsa_matrix = lsa.transform(query_term_matrix)

# Hybrid Scoring Function
def hybrid_score(query_index, query_vector):
    # BM25L scores
    query_tokens = df_pertanyaan['processed_pertanyaan'][query_index].split()
    bm25_scores = bm25l.get_scores(query_tokens)

    # LSA scores
    query_lsa_vec = query_lsa_matrix[query_index].reshape(1, -1)
    lsa_scores = cosine_similarity(query_lsa_vec, lsa_matrix_normalized).flatten()

    # Combine scores with a weight (e.g., 0.5 for each method)
    alpha = 0.5
    hybrid_scores = alpha * bm25_scores + (1 - alpha) * lsa_scores

    return hybrid_scores

# Evaluate Retrieval for Top-k
def evaluate_top_k(ground_truth_dict, query_id, ranked_indices, k):
    relevant_indices = ground_truth_dict.get(query_id, set())
    retrieved_indices = set(ranked_indices[:k])

    tp = len(retrieved_indices & relevant_indices)  # True Positives
    precision = tp / len(retrieved_indices) if len(retrieved_indices) > 0 else 0
    recall = tp / len(relevant_indices) if len(relevant_indices) > 0 else 0

    return precision, recall

# Evaluate for multiple top-k values
top_k_values = [5, 10, 20, 30, 40, 50, 60]
evaluation_results = {}

for i in range(len(df_pertanyaan)):
    query_id = f"Pertanyaan {i+1}"

    # Compute hybrid scores
    hybrid_scores = hybrid_score(i, query_lsa_matrix[i])

    # Rank documents based on hybrid scores
    ranked_indices = np.argsort(hybrid_scores)[::-1]

    # Evaluate for each top-k value
    evaluation_results[query_id] = {}
    for k in top_k_values:
        precision, recall = evaluate_top_k(ground_truth_dict, query_id, ranked_indices, k)
        evaluation_results[query_id][f"Top-{k}"] = {
            "Precision": precision,
            "Recall": recall
        }

# Calculate and display average Precision and Recall for each top-k
average_results = {f"Top-{k}": {"Precision": 0, "Recall": 0} for k in top_k_values}

for query_id, results in evaluation_results.items():
    for k in top_k_values:
        average_results[f"Top-{k}"]["Precision"] += results[f"Top-{k}"]["Precision"]
        average_results[f"Top-{k}"]["Recall"] += results[f"Top-{k}"]["Recall"]

for k in top_k_values:
    average_results[f"Top-{k}"]["Precision"] /= len(df_pertanyaan)
    average_results[f"Top-{k}"]["Recall"] /= len(df_pertanyaan)

# Display evaluation results for each query
for query_id, results in evaluation_results.items():
    print(f"\n{query_id}")
    for k, metrics in results.items():
        print(f"{k}: Precision = {metrics['Precision']:.2f}, Recall = {metrics['Recall']:.2f}")

# Display average results
print("\nAverage Results:")
for k, metrics in average_results.items():
    print(f"{k}: Precision = {metrics['Precision']:.2f}, Recall = {metrics['Recall']:.2f}")



Pertanyaan 1
Top-5: Precision = 1.00, Recall = 0.01
Top-10: Precision = 0.80, Recall = 0.01
Top-20: Precision = 0.75, Recall = 0.02
Top-30: Precision = 0.70, Recall = 0.03
Top-40: Precision = 0.75, Recall = 0.05
Top-50: Precision = 0.80, Recall = 0.07
Top-60: Precision = 0.82, Recall = 0.08

Pertanyaan 2
Top-5: Precision = 0.20, Recall = 0.50
Top-10: Precision = 0.10, Recall = 0.50
Top-20: Precision = 0.05, Recall = 0.50
Top-30: Precision = 0.03, Recall = 0.50
Top-40: Precision = 0.03, Recall = 0.50
Top-50: Precision = 0.02, Recall = 0.50
Top-60: Precision = 0.02, Recall = 0.50

Pertanyaan 3
Top-5: Precision = 1.00, Recall = 0.00
Top-10: Precision = 0.90, Recall = 0.00
Top-20: Precision = 0.95, Recall = 0.00
Top-30: Precision = 0.97, Recall = 0.01
Top-40: Precision = 0.97, Recall = 0.01
Top-50: Precision = 0.98, Recall = 0.01
Top-60: Precision = 0.98, Recall = 0.01

Pertanyaan 4
Top-5: Precision = 1.00, Recall = 0.00
Top-10: Precision = 0.90, Recall = 0.01
Top-20: Precision = 0.65, Re

## MPNET + BM25L

## Ontology + BM25L

In [37]:
# Fungsi untuk mendapatkan sinonim dari WordNet
def get_synonyms(word):
    synonyms = set()
    for syn in wordnet.synsets(word):
        for lemma in syn.lemmas():
            synonyms.add(lemma.name().replace('_', ' '))
    return list(synonyms)

In [38]:
# Fungsi untuk ekspansi kueri menggunakan WordNet
def expand_query_with_wordnet(query):
    expanded_query = query
    for word in query.split():
        synonyms = get_synonyms(word)
        expanded_query += " " + " ".join(synonyms)
    return expanded_query

In [39]:
# Implementasi BM25L
class BM25L:
    def __init__(self, corpus, b=0.75, k1=1.5, delta=0.5):
        self.corpus = [doc.split() for doc in corpus]
        self.b = b
        self.k1 = k1
        self.delta = delta
        self.doc_lengths = np.array([len(doc) for doc in self.corpus])
        self.avg_doc_length = np.mean(self.doc_lengths)
        self.doc_freqs = self._compute_doc_frequencies()
        self.idf = self._compute_idf()

    def _compute_doc_frequencies(self):
        freqs = {}
        for doc in self.corpus:
            for term in set(doc):
                if term not in freqs:
                    freqs[term] = 0
                freqs[term] += 1
        return freqs

    def _compute_idf(self):
        total_docs = len(self.corpus)
        return {
            term: np.log((total_docs - freq + 0.5) / (freq + 0.5) + 1)
            for term, freq in self.doc_freqs.items()
        }

    def _score(self, query, doc, doc_length):
        score = 0
        for term in query:
            if term in self.doc_freqs:
                idf = self.idf[term]
                freq = doc.count(term)
                norm_len = (1 - self.b) + self.b * (doc_length / self.avg_doc_length)
                numerator = freq * (self.k1 + 1)
                denominator = freq + self.k1 * norm_len + self.delta
                score += idf * (numerator / denominator)
        return score

    def get_scores(self, query):
        query = query.split()
        scores = [
            self._score(query, doc, doc_length)
            for doc, doc_length in zip(self.corpus, self.doc_lengths)
        ]
        return np.array(scores)



In [40]:
# Hybrid Search dengan RRF (Reciprocal Rank Fusion)
def hybrid_rrf(query, bm25_scores, tfidf_scores, k=60):
    rrf_scores = 1 / (50 + np.argsort(np.argsort(-bm25_scores)) + np.argsort(np.argsort(-tfidf_scores)))
    top_k_indices = np.argsort(-rrf_scores)[:k]
    return top_k_indices


In [41]:
# Ekspansi kueri
corpus = df['processed_text']
df_pertanyaan['expanded_query'] = df_pertanyaan['processed_pertanyaan'].apply(expand_query_with_wordnet)

# Vectorize dokumen dan kueri
vectorizer = TfidfVectorizer()
document_vectors = vectorizer.fit_transform(corpus)
query_vectors = vectorizer.transform(df_pertanyaan['expanded_query'])

In [42]:
# BM25L Search
bm25l = BM25L(corpus)


In [44]:
#Evaluasi
results = {}
averages = {top_k: {"Precision": 0, "Recall": 0} for top_k in [5, 10, 20, 30, 40, 50, 60]}
query_count = query_vectors.shape[0]

for query_id, query_vector in enumerate(query_vectors):
    query_key = f"Pertanyaan {query_id + 1}"
    results[query_key] = {}

    expanded_query = df_pertanyaan['expanded_query'].iloc[query_id]
    bm25_scores = bm25l.get_scores(expanded_query)
    tfidf_scores = cosine_similarity(query_vector, document_vectors).flatten()

    for top_k in [5, 10, 20, 30, 40, 50, 60]:
        retrieved_indices = hybrid_rrf(expanded_query, bm25_scores, tfidf_scores, k=top_k)
        precision, recall = evaluate_retrieval(ground_truth_dict, query_key, retrieved_indices)
        results[query_key][f"Top {top_k}"] = {
            "Precision": precision,
            "Recall": recall
        }
        averages[top_k]["Precision"] += precision
        averages[top_k]["Recall"] += recall


In [45]:
# Hitung rata-rata untuk masing-masing Top K
for top_k in averages:
    averages[top_k]["Precision"] /= query_count
    averages[top_k]["Recall"] /= query_count

# Tampilkan Hasil Evaluasi
import pprint
pprint.pprint(results)
print("\nRata-rata untuk masing-masing Top K:")
pprint.pprint(averages)

{'Pertanyaan 1': {'Top 10': {'Precision': 1.0, 'Recall': 0.016638935108153077},
                  'Top 20': {'Precision': 1.0, 'Recall': 0.033277870216306155},
                  'Top 30': {'Precision': 0.9666666666666667,
                             'Recall': 0.048252911813643926},
                  'Top 40': {'Precision': 0.975, 'Recall': 0.064891846921797},
                  'Top 5': {'Precision': 1.0, 'Recall': 0.008319467554076539},
                  'Top 50': {'Precision': 0.96, 'Recall': 0.07986688851913477},
                  'Top 60': {'Precision': 0.9333333333333333,
                             'Recall': 0.09317803660565724}},
 'Pertanyaan 10': {'Top 10': {'Precision': 0.8, 'Recall': 0.34782608695652173},
                   'Top 20': {'Precision': 0.6, 'Recall': 0.5217391304347826},
                   'Top 30': {'Precision': 0.5333333333333333,
                              'Recall': 0.6956521739130435},
                   'Top 40': {'Precision': 0.5, 'Recall': 0.86956521739

# Fine Tuning Best Model

In [46]:
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.feature_extraction.text import TfidfVectorizer
from nltk.corpus import wordnet
import nltk
import numpy as np
import pprint

# Pastikan resource NLTK sudah diunduh
nltk.download('wordnet')
nltk.download('omw-1.4')

# Fungsi untuk mendapatkan sinonim dari WordNet
def get_synonyms(word):
    synonyms = set()
    for syn in wordnet.synsets(word):
        for lemma in syn.lemmas():
            synonyms.add(lemma.name().replace('_', ' '))
    return list(synonyms)

# Fungsi untuk ekspansi kueri menggunakan WordNet
def expand_query_with_wordnet(query):
    expanded_query = query
    for word in query.split():
        synonyms = get_synonyms(word)
        expanded_query += " " + " ".join(synonyms)
    return expanded_query

# Preprocess kueri dengan ekspansi menggunakan WordNet
df_pertanyaan['expanded_query'] = df_pertanyaan['processed_pertanyaan'].apply(expand_query_with_wordnet)

# Vectorize dokumen dan kueri
vectorizer = TfidfVectorizer()

document_vectors = vectorizer.fit_transform(df['processed_text'])
query_vectors = vectorizer.transform(df_pertanyaan['expanded_query'])

# BM25L Implementation
class BM25L:
    def __init__(self, corpus, b=0.75, k1=1.5, delta=0.5):
        self.corpus = [doc.split() for doc in corpus]
        self.b = b
        self.k1 = k1
        self.delta = delta
        self.doc_lengths = np.array([len(doc) for doc in self.corpus])
        self.avg_doc_length = np.mean(self.doc_lengths)
        self.doc_freqs = self._compute_doc_frequencies()
        self.idf = self._compute_idf()

    def _compute_doc_frequencies(self):
        freqs = {}
        for doc in self.corpus:
            for term in set(doc):
                if term not in freqs:
                    freqs[term] = 0
                freqs[term] += 1
        return freqs

    def _compute_idf(self):
        total_docs = len(self.corpus)
        return {
            term: np.log((total_docs - freq + 0.5) / (freq + 0.5) + 1)
            for term, freq in self.doc_freqs.items()
        }

    def _score(self, query, doc, doc_length):
        score = 0
        for term in query:
            if term in self.doc_freqs:
                idf = self.idf[term]
                freq = doc.count(term)
                norm_len = (1 - self.b) + self.b * (doc_length / self.avg_doc_length)
                numerator = freq * (self.k1 + 1)
                denominator = freq + self.k1 * norm_len + self.delta
                score += idf * (numerator / denominator)
        return score

    def get_scores(self, query):
        query = query.split()
        scores = [
            self._score(query, doc, doc_length)
            for doc, doc_length in zip(self.corpus, self.doc_lengths)
        ]
        return np.array(scores)

# Fine-tuning Hybrid Model Parameters
bm25l = BM25L(df['processed_text'], b=0.75, k1=1.5, delta=0.5)

# Retrieve Top K Dokumen dengan hybrid

def hybrid_search(query_vector, bm25_scores, document_vectors, top_k, alpha=0.5):
    tfidf_scores = cosine_similarity(query_vector, document_vectors).flatten()
    hybrid_scores = alpha * tfidf_scores + (1 - alpha) * bm25_scores
    top_k_indices = hybrid_scores.argsort()[-top_k:][::-1]
    return top_k_indices

# Evaluasi untuk Top K (5, 10, 20, 30, 40, 50, 60)
results = {}
averages = {top_k: {"Precision": 0, "Recall": 0} for top_k in [5, 10, 20, 30, 40, 50, 60]}
query_count = query_vectors.shape[0]  # Menggunakan shape untuk mendapatkan jumlah kueri

for query_id, query_vector in enumerate(query_vectors):
    query_key = f"Pertanyaan {query_id + 1}"
    results[query_key] = {}

    # Dapatkan skor BM25L untuk kueri asli
    bm25_scores = bm25l.get_scores(df_pertanyaan['processed_pertanyaan'][query_id])

    for top_k in [5, 10, 20, 30, 40, 50, 60]:
        retrieved_indices = hybrid_search(query_vector, bm25_scores, document_vectors, top_k, alpha=0.7)
        precision, recall = evaluate_retrieval(ground_truth_dict, query_key, retrieved_indices)
        results[query_key][f"Top {top_k}"] = {
            "Precision": precision,
            "Recall": recall
        }
        averages[top_k]["Precision"] += precision
        averages[top_k]["Recall"] += recall

# Hitung rata-rata untuk masing-masing Top K
for top_k in averages:
    averages[top_k]["Precision"] /= query_count
    averages[top_k]["Recall"] /= query_count

# Tampilkan Hasil Evaluasi
pprint.pprint(results)
print("\nRata-rata untuk masing-masing Top K:")
pprint.pprint(averages)


[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\acer\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package omw-1.4 to
[nltk_data]     C:\Users\acer\AppData\Roaming\nltk_data...
[nltk_data]   Package omw-1.4 is already up-to-date!


{'Pertanyaan 1': {'Top 10': {'Precision': 1.0, 'Recall': 0.016638935108153077},
                  'Top 20': {'Precision': 0.95, 'Recall': 0.03161397670549085},
                  'Top 30': {'Precision': 0.9333333333333333,
                             'Recall': 0.04658901830282862},
                  'Top 40': {'Precision': 0.9, 'Recall': 0.059900166389351084},
                  'Top 5': {'Precision': 1.0, 'Recall': 0.008319467554076539},
                  'Top 50': {'Precision': 0.88, 'Recall': 0.07321131447587355},
                  'Top 60': {'Precision': 0.8833333333333333,
                             'Recall': 0.08818635607321132}},
 'Pertanyaan 10': {'Top 10': {'Precision': 0.8, 'Recall': 0.34782608695652173},
                   'Top 20': {'Precision': 0.6, 'Recall': 0.5217391304347826},
                   'Top 30': {'Precision': 0.6333333333333333,
                              'Recall': 0.8260869565217391},
                   'Top 40': {'Precision': 0.5, 'Recall': 0.86956521739

## MPNet + BM25L

In [10]:
import numpy as np
from rank_bm25 import BM25L
from transformers import AutoTokenizer, AutoModel
import torch
from sklearn.preprocessing import normalize

# Load MPNet model and tokenizer
mpnet_model_name = "sentence-transformers/all-mpnet-base-v2"
tokenizer = AutoTokenizer.from_pretrained(mpnet_model_name)
model = AutoModel.from_pretrained(mpnet_model_name)

# Helper function to compute embeddings with MPNet
def compute_mpnet_embeddings(texts):
    inputs = tokenizer(texts, padding=True, truncation=True, return_tensors="pt")
    with torch.no_grad():
        model_output = model(**inputs)
    embeddings = model_output.last_hidden_state.mean(dim=1)
    return embeddings.cpu().numpy()

# Preprocess queries and documents
queries = df_pertanyaan['processed_pertanyaan'].tolist()
documents = df['processed_text'].tolist()

# Compute MPNet embeddings for documents
document_embeddings = compute_mpnet_embeddings(documents)

# Initialize BM25L
bm25 = BM25L([doc.split() for doc in documents])

RuntimeError: [enforce fail at alloc_cpu.cpp:114] data. DefaultCPUAllocator: not enough memory: you tried to allocate 8155299840 bytes.

In [ ]:
# Hybrid retrieval function
def hybrid_retrieval(query, document_embeddings, documents, top_k=10, alpha=0.5):
    # Compute MPNet embedding for the query
    query_embedding = compute_mpnet_embeddings([query])[0]

    # Compute cosine similarity for MPNet
    cosine_similarities = np.dot(document_embeddings, query_embedding)
    cosine_similarities = normalize(cosine_similarities.reshape(1, -1), norm='l2')[0]

    # Compute BM25L scores
    bm25_scores = bm25.get_scores(query.split())

    # Combine scores using the hybrid formula
    hybrid_scores = alpha * cosine_similarities + (1 - alpha) * bm25_scores

    # Get top-k results
    top_indices = np.argsort(hybrid_scores)[::-1][:top_k]
    return top_indices

# Evaluate retrieval results
def evaluate_hybrid(ground_truth_dict, queries, document_embeddings, documents, top_ks):
    results = {}

    for top_k in top_ks:
        precisions, recalls = [], []

        for i, query in enumerate(queries):
            query_id = f"Pertanyaan {i + 1}"

            if query_id in ground_truth_dict:
                retrieved_indices = hybrid_retrieval(query, document_embeddings, documents, top_k=top_k)
                precision, recall = evaluate_retrieval(ground_truth_dict, query_id, retrieved_indices)
                precisions.append(precision)
                recalls.append(recall)

        # Compute average precision and recall for the current top_k
        avg_precision = np.mean(precisions)
        avg_recall = np.mean(recalls)
        results[top_k] = {
            "precision": avg_precision,
            "recall": avg_recall
        }

    return results

# Define top_k values to evaluate
top_ks = [5, 10, 20, 30, 40, 50, 60]

# Perform evaluation
evaluation_results = evaluate_hybrid(ground_truth_dict, queries, document_embeddings, documents, top_ks)

# Display results
for top_k, metrics in evaluation_results.items():
    print(f"Top-{top_k} -> Precision: {metrics['precision']:.4f}, Recall: {metrics['recall']:.4f}")


RuntimeError: [enforce fail at alloc_cpu.cpp:114] data. DefaultCPUAllocator: not enough memory: you tried to allocate 8155299840 bytes.